# Riemann scheme. 

In [1]:
# Importing relevant libraries 
import numpy as np
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# plt.style.use('dark_background')
plt.style.use('default')

Lets consider same setup as in [ex_3a](https://github.com/AST-Course/AST5110/blob/main/ex_3a.ipynb) Burgers’ equation, i.e.,

$$\frac{\partial u}{\partial t} + u \frac{\partial u}{\partial x} = 0   \tag{1}$$ 

for the domain $x \in (x_0, x_f)$ with $x_0 = −1.4$, $x_f = 2.0$ with initial condition:

$$u(x,t=0) = A\left[\tanh\left(\frac{x+x_c}{W}\right)-\tanh\left(\frac{x-x_c}{W}\right)\right]   \tag{2}$$

whereby $A = 0.02$ , $x_c = 0.70$, $W = 0.1$. Let the solution evolve until time $t_f = 100$. However, let's now implement a new time-step method. Find the conservative form of the equation and implement a Rieman solver [wiki:Rieman Solvers](https://github.com/AST-Course/AST5110/wiki/Riemann-solvers). 

Add this to your library and solve the previous simulation imposing the CFL condition. For this exercise, fill in `nm_lib` the function `evolv_Rie_uadv_burgers`. 

In [2]:
x0 = -1.4 
xf = 2.0 

def u(x, A=0.02): 
    """ 
    Initial condition for t=t0 when a = const

    Parameters
    ----------
    x : `array`
        Spatial axis. 
    A : `float`
        A constant of the initial condition (default = 0.02).
    
    Returns
    -------
    Equation 2
    """
    xc = 0.70
    W = 0.1 
    return A*(np.tanh((x+xc) / W) - np.tanh((x-xc) / W))

tf = 100*2
nt = tf

<span style="color:pink">
To start, we have to rewrite eq. 1) to the conservative form. Scalar converion laws have a conservative form 

$$
    \frac{\partial u}{\partial t} + \frac{\partial}{\partial x} [F(u(x,t))] = 0
$$

To find the conservative form from the non-conservative form, we find the flux by equating the appropriate terms: 
$$
    \frac{\partial}{\partial x}(F(u)) = A(u)\frac{\partial u}{\partial x}
$$

The left hand side is given by the definition of a function of a function 
$$
\frac{\partial}{\partial x}(F(u(x,t))) = \frac{\partial F}{\partial u}\frac{\partial u}{\partial x} = A(u)\frac{\partial u}{\partial x}
$$

In the case of eq. 1), we identify that $A(u) = \frac{\partial F}{\partial u} = u$, and by integration we find that the flux $F(u)$ is 
$$
F(u) = \int A(u) du = \int u du = \frac{u^2}{2}
$$
Thus, the conservative form is: 
$$
\frac{\partial u}{\partial t} + u \frac{\partial }{\partial x}\left(\frac{u^2}{2}\right) = 0. 
$$

We may now implement the steps outlined below into the function `evolv_Rie_uadv_burgers` in `nm_lib`. 
</span>

#### 1 step
Compute left and right of $u$, i.e., $u_L$ and $u_R$

#### 2 step
Compute from those the flux, i.e., $F_L$ and $F_R$

<span style="color:pink">
Using the expression for the flux we found above, we have that 
    
$$
F(u_L) = \frac{u_L^2}{2}, \:\:\: F(u_R) = \frac{u_R^2}{2}
$$
</span>

#### 3 step
Compute the propagating speed ($v_a[i]=max(|u[i],|u[i-1]|)$)

#### 4 step
Compute the interface fluxes (Rusanov)

$rhs=(F_R+F_L)/2 - v_a (U_R -U_L)$

#### 5 step
Advance in time $u^{n+1}=u^n + dt\times rhs$. What is dt? 


In [3]:
nint = 128
nump = nint +1 

xx = np.arange(nump)/(nump-1.0) * (xf-x0) + x0

t_rie, unnt_rie = nm.evolv_Rie_uadv_burgers(xx, u(xx), nt, ddx=nm.deriv_upw, bnd_limits=[1,0])
t_lax, unnt_lax = nm.evolv_Lax_uadv_burgers(xx, u(xx), nt, ddx=nm.deriv_upw, bnd_limits=[1,0])

In [4]:
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(xx, unnt_rie[:,0])
    axes.plot(xx, unnt_lax[:,0])

def animate(i):
    axes.clear()
    axes.plot(xx, unnt_rie[:,i], label='Rie')
    axes.plot(xx, unnt_lax[:,i], label='Lax')
    axes.legend()
    axes.set_ylim((0, 0.05))
    axes.set_title('t=%.2f'%t_lax[i])
    axes.grid(True)
    
anim = FuncAnimation(fig, animate, interval=1, frames=nt, init_func=init)
plt.close()
HTML(anim.to_jshtml())


compare relations etweeb pixels i and i+1 assuming onw is over and one is under (left,right)
how much flux goes to the side 


comparison might be off 


<span style="color:pink">
j
</span>

Is this method less or more diffusive than Lax method? Find the analytical solution and compare. Where and when is better or worse than the Lax method? 

---
## TVD scheme. 

Combine the Lax method with the Rieman solver using a flux limiter scheme. For this, one needs to identify how large are the gradients. Lets define: 

$$r^{+}_i = \frac{u_i-u_{i-1}}{u_{i+1}+u_i}$$

What kind of properties do you see on $r^{+}_i$? e.g., what happens when $r\ge0$? or $r\le0$? 

now lets consider the following flux limiter: 

$$\phi = max\left(0,min\left(\theta r,\frac{1+r}{2},\theta \right)\right),\, \theta =[1,2]$$

Finally, combine the Lax from previous excersice with the Riemann solver using the flux limiter as follows: 

$$u^{n+1}_i = u^n_i + dt (f^n_{i+1/2}-f^n_{i-1/2})$$

Where 

$$f^n_{i+1/2} = f^{Riemann}_{i+1/2} + \phi^n_i (f^{L}_{i+1/2}-f^{Riemann}_{i+1/2})$$



When becomes purely Rieman solver? And Lax? Which others methods you can find depending on what is $r$ of $\phi$. 

What would be the corrective numerical flux in order to be a flux-limited?